
# Tensor field sensors in 3D

This example demonstrates the application of the `pyvale` sensor simulation
module to tensor fields in 3 spatial dimensions. An example of a vector field
sensor would be a displacement transducer, point tracking or velocity sensor.

Note that this example has minimal explanation and assumes you have reviewed the
basic sensor simulation examples to understand how the underlying engine works
as well as the sensor simulation workflow.


In [ ]:
from pathlib import Path
import numpy as np
import matplotlib.pyplot as plt
from scipy.spatial.transform import Rotation

# pyvale imports
import pyvale.mooseherder as mh
import pyvale.sensorsim as sens
import pyvale.dataset as dataset

## 1. Load physics simulation data



In [ ]:
data_path: Path = dataset.element_case_output_path(dataset.EElemTest.HEX20)
sim_data: mh.SimData = mh.ExodusLoader(data_path).load_all_sim_data()

disp_keys = ("disp_x","disp_y","disp_z")
norm_comp_keys = ("strain_xx","strain_yy","strain_zz")
dev_comp_keys = ("strain_xy","strain_yz","strain_xz")

sim_data: mh.SimData = sens.scale_length_units(scale=1000.0,
                                               sim_data=sim_data,
                                               disp_keys=disp_keys)

## 2. Build virtual sensor arrays



In [ ]:
# Simulations is a 10mm cube
sensor_positions = np.array(((5.0,0.0,5.0),     # cube x-z face
                             (5.0,10.0,5.0),    # cube x-z face
                             (5.0,5.0,0.0),     # cube x-y face
                             (5.0,5.0,10.0),    # cube x-y face
                             (0.0,5.0,5.0),     # cube y-z face
                             (10.0,5.0,5.0),))  # cube y-z face

sample_times = np.linspace(0.0,np.max(sim_data.time),50)

sens_angles = (Rotation.from_euler("zyx", [0, 0, 0], degrees=True),
               Rotation.from_euler("zyx", [0, 0, 0], degrees=True),
               Rotation.from_euler("zyx", [45, 0, 0], degrees=True),
               Rotation.from_euler("zyx", [45, 0, 0], degrees=True),
               Rotation.from_euler("zyx", [0, 0, 45], degrees=True),
               Rotation.from_euler("zyx", [0, 0, 45], degrees=True),)


sens_data = sens.SensorData(positions=sensor_positions,
                            sample_times=sample_times,
                            angles=sens_angles)

descriptor = sens.SensorDescriptor(name="Strain",
                                   symbol=r"\varepsilon",
                                   units=r"-",
                                   tag="SG",
                                   components=('xx','yy','zz','xy','yz','xz'))

sens_array: sens.SensorsPoint = sens.SensorFactory.tensor_point(
    sim_data,
    sens_data,
    norm_comp_keys=norm_comp_keys,
    dev_comp_keys=dev_comp_keys,
    spatial_dims=sens.EDim.THREED,
    descriptor=descriptor,
)

### 2.1. Add simulated measurement errors



In [ ]:
pos_uncert = 0.1 # units = mm
pos_rand_xyz = (sens.GenNormal(std=pos_uncert),
                sens.GenNormal(std=pos_uncert),
                sens.GenNormal(std=pos_uncert))

angle_uncert = 2.0 # units = degrees
angle_rand_zyx = (sens.GenUniform(low=-angle_uncert,high=angle_uncert),
                  sens.GenUniform(low=-angle_uncert,high=angle_uncert),
                  sens.GenUniform(low=-angle_uncert,high=angle_uncert))

pos_lock = np.full(sensor_positions.shape,False,dtype=bool)
pos_lock[0:2,1] = True   # block translation in y
pos_lock[2:4,2] = True   # block translation in z
pos_lock[4:6,0] = True   # block translation in x

angle_lock = np.full(sensor_positions.shape,True,dtype=bool)
angle_lock[0:2,1] = False   # allow rotation about y
angle_lock[2:4,0] = False   # allow rotation about z
angle_lock[4:6,2] = False   # allow rotation about x

field_error_data = sens.ErrFieldData(pos_rand_xyz=pos_rand_xyz,
                                     pos_lock_xyz=pos_lock,
                                     ang_rand_zyx=angle_rand_zyx,
                                     ang_lock_zyx=angle_lock)

error_chain: list[sens.IErrSimulator] = [
    sens.ErrSysGenPercent(sens.GenUniform(low=-1.0,high=1.0)),
    sens.ErrRandGenPercent(sens.GenNormal(std=1.0)),
    sens.ErrSysField(sens_array.get_field(),field_error_data),
]

sens_array.set_error_chain(error_chain)

## 3. Create & run simulated experiment



In [ ]:
measurements: np.ndarray = sens_array.sim_measurements()

truth: np.ndarray = sens_array.get_truth()
sys_errs: np.ndarray = sens_array.get_errors_systematic()
rand_errs: np.ndarray = sens_array.get_errors_random()

print(80*"-")
print("measurement = truth + sysematic error + random error")

print(f"measurements.shape = {measurements.shape} = "
        + "(n_sensors,n_field_components,n_timesteps)")
print(f"truth.shape     = {truth.shape}")
print(f"sys_errs.shape  = {sys_errs.shape}")
print(f"rand_errs.shape = {rand_errs.shape}")

sens_print: int = 2
comp_print: int = 1
time_last: int = 5
time_print = slice(measurements.shape[2]-time_last,measurements.shape[2])

print(f"\nThese are the last {time_last} virtual measurements of sensor "
        + f"{sens_print}:\n")

sens.print_measurements(sens_array,sens_print,comp_print,time_print)
print("\n"+80*"-")

## 4. Analyse & visualise the results



In [ ]:
output_path = Path.cwd() / "pyvale-output"
if not output_path.is_dir():
    output_path.mkdir(parents=True, exist_ok=True)

for kk in (norm_comp_keys+dev_comp_keys):
    pv_plot = sens.plot_point_sensors_on_sim(sens_array,kk)
    pv_plot.camera_position = "yz"
    pv_plot.camera.azimuth = 45
    pv_plot.camera.elevation = 45

    # Set to False to show an interactive plot instead of saving the figure
    pv_plot.off_screen = True
    if pv_plot.off_screen:
        pv_plot.screenshot(output_path/f"ext_ex3f_locs_{kk}.png")
    else:
        pv_plot.show()

<img src="file://../../../../_static/ext_ex3f_locs_strain_yy.png" alt="Virtual sensor location visualisation." width="800px" align="center">



In [ ]:
for kk in (norm_comp_keys+dev_comp_keys):
    (fig,ax) = sens.plot_time_traces(sens_array,comp_key=kk)
    fig.savefig(output_path/f"ext_ex3f_traces_{kk}.png",
                dpi=300,
                bbox_inches="tight")

# Uncomment this to display the sensor trace plot
# plt.show()

<img src="file://../../../../_static/ext_ex3f_traces_strain_yy.png" alt="Simulated sensor traces." width="600px" align="center">

